#Prediction of Covid_19 cases in Future

In [447]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [448]:
#Importing Packages
import pandas as pd
import numpy as np
import pandas as pd
import matplotlib
import matplotlib.pyplot as pp
import matplotlib.pyplot as plt
import seaborn as sns
import sklearn 
import math
import time
from sklearn.model_selection import RandomizedSearchCV, train_test_split
from sklearn.svm import SVR
from sklearn.metrics import mean_squared_error, mean_absolute_error
import datetime

%matplotlib inline

In [449]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)



#read the data and store data titled time_series_covid19_confirmed_global.csv
covid_19_trend = ('/content/drive/My Drive/Stomble_Task/time_series_covid19_confirmed_global.csv')
confirmed_cases_df = pd.read_csv(covid_19_trend) 
confirmed_cases_df.head()

Province/State Country/Region       Lat  ...  2/15/21  2/16/21  2/17/21
0            NaN    Afghanistan  33.93911  ...    55514    55518    55540
1            NaN        Albania  41.15330  ...    93850    94651    95726
2            NaN        Algeria  28.03390  ...   110894   111069   111247
3            NaN        Andorra  42.50630  ...    10538    10555    10583
4            NaN         Angola -11.20270  ...    20381    20389    20400

[5 rows x 397 columns]

In [450]:
#shape of the data
confirmed_cases_df.shape


(273, 397)

In [451]:
#describinh the data
confirmed_cases_df.describe

<bound method NDFrame.describe of     Province/State      Country/Region        Lat  ...  2/15/21  2/16/21  2/17/21
0              NaN         Afghanistan  33.939110  ...    55514    55518    55540
1              NaN             Albania  41.153300  ...    93850    94651    95726
2              NaN             Algeria  28.033900  ...   110894   111069   111247
3              NaN             Andorra  42.506300  ...    10538    10555    10583
4              NaN              Angola -11.202700  ...    20381    20389    20400
..             ...                 ...        ...  ...      ...      ...      ...
268            NaN             Vietnam  14.058324  ...     2269     2311     2329
269            NaN  West Bank and Gaza  31.952200  ...   168444   169487   170527
270            NaN               Yemen  15.552727  ...     2145     2148     2151
271            NaN              Zambia -13.133897  ...    70248    70823    71677
272            NaN            Zimbabwe -19.015438  ...    35222 



```

```

## Data Visualization of Number of Cases-Covid-19 in World-wide

## Data PreProcessing

In [452]:
confirmed_cases_df.rename(columns={"Province/State": "Province_State", "Country/Region": "Country_Region"}, inplace=True)

In [453]:
#changing the dataframe format from wide to long using melt() function
confirmed_cases_melt_df = pd.melt(confirmed_cases_df, id_vars=['Province_State', 'Country_Region', 'Lat', 'Long'],
                          var_name = 'Date',
                          value_name = 'Confirmed_cases')
confirmed_cases_melt_df

Province_State      Country_Region  ...     Date  Confirmed_cases
0                 NaN         Afghanistan  ...  1/22/20                0
1                 NaN             Albania  ...  1/22/20                0
2                 NaN             Algeria  ...  1/22/20                0
3                 NaN             Andorra  ...  1/22/20                0
4                 NaN              Angola  ...  1/22/20                0
...               ...                 ...  ...      ...              ...
107284            NaN             Vietnam  ...  2/17/21             2329
107285            NaN  West Bank and Gaza  ...  2/17/21           170527
107286            NaN               Yemen  ...  2/17/21             2151
107287            NaN              Zambia  ...  2/17/21            71677
107288            NaN            Zimbabwe  ...  2/17/21            35423

[107289 rows x 6 columns]

In [454]:
#shape of the changed format
confirmed_cases_melt_df.shape


(107289, 6)

In [455]:
confirmed_cases_melt_df.index

RangeIndex(start=0, stop=107289, step=1)

In [456]:
#checking for missing values
confirmed_cases_melt_df.isnull().sum()

Province_State     74277
Country_Region         0
Lat                  393
Long                 393
Date                   0
Confirmed_cases        0
dtype: int64

In [457]:
#dsiplaying the columns in the dataset
confirmed_cases_melt_df.columns

Index(['Province_State', 'Country_Region', 'Lat', 'Long', 'Date',
       'Confirmed_cases'],
      dtype='object')

In [458]:
#Dropping the Repatriated Travellers as there is a missing values for Lat and Long
confirmed_cases_melt_df.dropna(axis=0, subset=['Lat'])
confirmed_cases_melt_df.dropna(axis=0, subset=['Long'])
confirmed_cases_melt_df

Province_State      Country_Region  ...     Date  Confirmed_cases
0                 NaN         Afghanistan  ...  1/22/20                0
1                 NaN             Albania  ...  1/22/20                0
2                 NaN             Algeria  ...  1/22/20                0
3                 NaN             Andorra  ...  1/22/20                0
4                 NaN              Angola  ...  1/22/20                0
...               ...                 ...  ...      ...              ...
107284            NaN             Vietnam  ...  2/17/21             2329
107285            NaN  West Bank and Gaza  ...  2/17/21           170527
107286            NaN               Yemen  ...  2/17/21             2151
107287            NaN              Zambia  ...  2/17/21            71677
107288            NaN            Zimbabwe  ...  2/17/21            35423

[107289 rows x 6 columns]

In [459]:
import plotly.express as px
fig = px.density_mapbox(confirmed_cases_melt_df, 
                        lat="Lat", 
                        lon="Long", 
                        hover_name="Province_State", 
                        hover_data=["Confirmed_cases"], 
                        animation_frame="Date",
                        color_continuous_scale="Portland",
                        radius=7, 
                        zoom=0,height=1000)
fig.update_layout(title='Worldwide Corona Virus Cases Time Lapse - Confirmed, Deaths, Recovered',
                  font=dict(family="Courier New, monospace",
                            size=18,
                            color="#7f7f7f")
                 )
fig.update_layout(mapbox_style="open-street-map", mapbox_center_lon=0)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})


fig.show()

### Number of samples per country in our data

In [460]:
# Top 50 Country wise Confirmed cases acc to given data

fig, ax = plt.subplots(figsize=(10, 13))
sns.barplot(y=top_10.index[:50], x=top_10.values[:50])

**According to the bar graph, the graph shows a clear visualization of the Top 50 Country wise Confirmed cases from to given data. United States, India, Brazil are the top 3 highest number of covid-19 cases whereas, Belarus, Dominican Republic and Jordan has least number of covid-19 cases reported.**

In [470]:
#heat maps to generate correlation matrix of the confirmed cases for the covid-19
fig, ax = plt.subplots(figsize=(12, 8))
corr = confirmed_cases_melt_df.corr()
sns.heatmap(corr, linewidths=.5, cbar_kws={"shrink": .5},annot=True)

**According the coorelation matrix, there is a dependence of the variables from the dataset. According to the dataset, there is a dependence of Latitude and Country/Region variables which are to the important factors to be considered to predcit the number of covid-19 cases.**

In [462]:

#typecasting the categorical features to a category dtype
confirmed_cases_melt_df['Province_State'] = confirmed_cases_melt_df['Province_State'].astype('category').cat.codes
confirmed_cases_melt_df['Country_Region'] = confirmed_cases_melt_df['Country_Region'].astype('category').cat.codes

print(confirmed_cases_melt_df.dtypes)

Province_State        int8
Country_Region       int16
Lat                float64
Long               float64
Date                object
Confirmed_cases      int64
dtype: object


##Prediction of Number of Covid-19 cases from March 2021 to December 20201

In [463]:
confirmed_cases_melt_df.head()


Province_State  Country_Region  ...     Date  Confirmed_cases
0              -1               0  ...  1/22/20                0
1              -1               1  ...  1/22/20                0
2              -1               2  ...  1/22/20                0
3              -1               3  ...  1/22/20                0
4              -1               4  ...  1/22/20                0

[5 rows x 6 columns]

In [464]:
confirmed_cases_melt_df.columns = ['Province_State','Country_Region','Lat','Long','ds','y']
#confirmed['ds'] = confirmed['ds'].dt.date
confirmed_cases_melt_df['ds'] = pd.to_datetime(confirmed_cases_melt_df['ds'])

In [465]:
confirmed_cases_melt_df.head()

Province_State  Country_Region       Lat       Long         ds  y
0              -1               0  33.93911  67.709953 2020-01-22  0
1              -1               1  41.15330  20.168300 2020-01-22  0
2              -1               2  28.03390   1.659600 2020-01-22  0
3              -1               3  42.50630   1.521800 2020-01-22  0
4              -1               4 -11.20270  17.873900 2020-01-22  0

##Forecasting Number of Covid-19 Cases

In [466]:
days_to_forecast = 1 # changable
first_forecasted_date = sorted(list(set(confirmed_cases_melt_df['ds'].values)))[-days_to_forecast]

print('The first date to perform forecasts for is: ' + str(first_forecasted_date))

The first date to perform forecasts for is: 2021-02-17T00:00:00.000000000


In [476]:
from fbprophet import Prophet

m = Prophet(daily_seasonality=False, weekly_seasonality=False, yearly_seasonality=False)
#m.add_seasonality(name='monthly', period=30.5, fourier_order=5)
m.fit(confirmed_cases_melt_df)
future = m.make_future_dataframe(periods=5, freq = 'M')
future_confirmed = future.copy() # for non-baseline predictions later on
future.tail()


ds
393 2021-02-28
394 2021-03-31
395 2021-04-30
396 2021-05-31
397 2021-06-30

In [472]:
forecast = m.predict(future)
forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail()

ds           yhat     yhat_lower    yhat_upper
393 2021-02-28  439585.453928 -557560.530381  1.567822e+06
394 2021-03-31  510772.113537 -539796.933925  1.602321e+06
395 2021-04-30  579662.429289 -465614.676392  1.598058e+06
396 2021-05-31  650849.088898 -433578.026233  1.740928e+06
397 2021-06-30  719739.404649 -277460.831052  1.729807e+06

In [473]:
#plotting the prediction graph
forecast_components = m.plot_components(forecast)

**From the forecast component plots, it is clear that, there is an upward trend from May 2020 which is expontentially increasing, especially in the month of July. Hence, according to the prediction of the covid-19 dataset, there are chances of increasing number of cases in future.**


